# Pre-Processing BattLeDIM Data

Quick notebook version of the `import_model.py` program for easier visualisation

## Module Import

In [1]:
'''

+-------------------------------+
|                               |
|    I M P O R T   M O D E L    | 
|                               |
+-------------------------------+

Description

Created on Mon Jul  5 18:47:11 2021

@author: gardar
'''

# --------------------------
# Importing public libraries
# --------------------------

# Operating system specific functions
import os

# Argument parser, for configuring the program execution
import argparse

# An object oriented library for handling EPANET files in Python
import epynet 

# yaml / yml configuration file support (a kind of language) 
# pip install pyyaml
import yaml

# PyTorch deep learning framework
import torch

# Import the networkx library
import networkx as nx

# Import Pandas for data handling
import pandas as pd

# Import numpy for array handling
import numpy as np

# Matplotlib for generating graphics
import matplotlib.pyplot as plt

# PyTorch from graph conversion tool
from torch_geometric.utils import from_networkx

# conda install pytorch-sparse -c pyg

# Train-test split with shuffle 
from sklearn.model_selection import train_test_split

/home/zczlx79/.conda/envs/pytorch/lib/python3.7/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Custom Modules

In [3]:
# --------------------------
# Importing custom libraries
# --------------------------

# Import a custom tool for converting EPANET .inp files to networkx graphs
from utils.epanet_loader import get_nx_graph

# Function for visualisationa
from utils.visualisation import visualise

# EPANET simulator, used to generate nodal pressures from the nominal model
from utils.epanet_simulator import epanetSimulator

# SCADA timeseries dataloader
from utils.data_loader import battledimLoader, dataCleaner, dataGenerator

# PyTorch early stopping callback
from utils.early_stopping import EarlyStopping

# Metrics
from utils.metrics import Metrics


## Environment Paths

In [4]:
path_to_wdn = './data/L-TOWN.inp' # Do I need to distinguish between REAL and NOMINAL EPANET inps here? 

## `EPANET` Model Import

In [5]:
# Import the .inp file using the EPYNET library
wdn = epynet.Network(path_to_wdn)

# Solve hydraulic model for a single timestep
wdn.solve()

ENtoolkitError: Error 302: cannot open input file

## `networkx` Graph Conversion

In [5]:
# Convert the file using a custom function, based on:
# https://github.com/BME-SmartLab/GraphConvWat 
# G: Graph in nx format; pos: node position; head: hydraulic heads which not used in this project
G , pos , head = get_nx_graph(wdn, weight_mode='pipe_length', get_head=True)

In [6]:
"""
colormap  = (head - head.min()) / (head.max() - head.min()) # Try standard scaling
# Generate a colormap
cmap  = plt.get_cmap('hot')

# Fit the datapoints to the colormap
color = cmap(colormap)

# Visualise the the model using our visualisation utility
axis = visualise(G, pos=pos, color = color, edge_labels=True)
plt.savefig('./figure/head.pdf')
# plt.show()
"""

"\ncolormap  = (head - head.min()) / (head.max() - head.min()) # Try standard scaling\n# Generate a colormap\ncmap  = plt.get_cmap('hot')\n\n# Fit the datapoints to the colormap\ncolor = cmap(colormap)\n\n# Visualise the the model using our visualisation utility\naxis = visualise(G, pos=pos, color = color, edge_labels=True)\nplt.savefig('./figure/head.pdf')\n# plt.show()\n"

## Configuration File Import-->find the nodes with pressure sensor

In [7]:
'''
"dataset_configuration.yalm" :
Configuration file for generating the Historical (2018) and Evaluation (2019) datasets of the BattLeDIM competition.
Contains:
-file name of network
-dataset start and end times
-leakage information (link ID, start Time, end Time, leak Diameter (m), leak Type, peak Time)
-sensor locations (link or node IDs)
'''
print('Importing dataset configuration...\n')

# Open the dataset configuration file
with open('./data/dataset_configuration.yaml') as file:

    # Load the configuration to a dictionary
    config = yaml.load(file, Loader=yaml.FullLoader)

# Generate a list of integers, indicating the number of the node
# at which a  pressure sensor is present
sensors = [int(string.replace("n", "")) for string in config['pressure_sensors']]

Importing dataset configuration...



## Visualisation

In [8]:
# Plot node with diff colors for with/without sensors
colormap = pd.Series([1.0 if i in sensors else 0.0 for i in range(1,G.number_of_nodes()+1)])

# Generate a colormap
cmap  = plt.get_cmap('coolwarm')

# Fit the datapoints to the colormap
color = cmap(colormap)

# Visualise the the model using our visualisation utility
axis = visualise(G, pos=pos, color = color, figsize = (60,32), edge_labels=True)
plt.savefig('./figure/graph_edge_pipe_length.pdf')
plt.savefig('./figure/graph_edge_pipe_length.png')
# plt.show()

## Graph Measurements

In [9]:
# We may want to find the largest subgraph diameter
largest_subgraph_diameter = 0

# For each component of the imported network
for i,c in enumerate(nx.connected_components(G)):
    graph = G.subgraph(c)                       # Generate a subgraph
    diameter = nx.diameter(graph)               # Measure its diameter
    print("Subgraph's {} diameter: \t {}".format(i+1,diameter))
    if diameter > largest_subgraph_diameter:    # If it's the longest encountered
        diameter = largest_subgraph_diameter    # Store it  
       

Subgraph's 1 diameter: 	 20
Subgraph's 2 diameter: 	 79


## SCADA Dataset

In [ ]:
import pandas as pd
import datetime
from scipy.sparse import csr_matrix
import pickle as pkl

In [35]:
len(G.edges)

905

In [11]:
# G.nodes # 1-782

In [21]:
df_pressure = pd.read_csv('./data/2018_SCADA_Pressures.csv', sep=';', decimal=',')

In [14]:
# Load the data into a numpy array with format matching the GraphConvWat problem
pressure_2018 = battledimLoader(observed_nodes = sensors,
                                n_nodes        = 782,
                                path           = './data/',
                                file           = '2018_SCADA_Pressures.csv')

# Print information and instructions about the imported data
msg = "The imported sensor data has shape (i,n,d): {}".format(pressure_2018.shape)

print(msg + "\n" + len(msg)*"-" + "\n")
print("Where: ")
print("'i' is the number of observations: {}".format(pressure_2018.shape[0]))
print("'n' is the number of nodes: {}".format(pressure_2018.shape[1]))
print("'d' is a {}-dimensional vector consisting of the pressure value and a mask ".format(pressure_2018.shape[2]))
print("The mask is set to '1' on observed nodes and '0' otherwise\n")

print("\n" + len(msg)*"-" + "\n")

The imported sensor data has shape (i,n,d): (105120, 782, 2)
------------------------------------------------------------

Where: 
'i' is the number of observations: 105120
'n' is the number of nodes: 782
'd' is a 2-dimensional vector consisting of the pressure value and a mask 
The mask is set to '1' on observed nodes and '0' otherwise


------------------------------------------------------------



In [15]:
# print('Pressure sensors in the network are located at nodes: ')
# for each in sensors:
#     print('Node: \t {}'.format(each))

In [37]:
df_pressure_new = pd.DataFrame(pressure_2018[:,:,0])

In [38]:
df_pressure_new['datetime'] = df_pressure['Timestamp']

In [39]:
df_pressure_new

0    1    2      3    4    5    6    7    8    9  ...  773  774  \
0       28.92  0.0  0.0  33.87  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
1       28.94  0.0  0.0  33.89  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
2       28.96  0.0  0.0  33.91  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
3       28.98  0.0  0.0  33.93  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
4       28.98  0.0  0.0  33.93  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
...       ...  ...  ...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
105115  28.55  0.0  0.0  33.61  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
105116  28.56  0.0  0.0  33.61  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
105117  28.58  0.0  0.0  33.64  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
105118  28.58  0.0  0.0  33.64  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
105119  28.63  0.0  0.0  33.68  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   

        775  776  777  778  779  780  781             datetime  
0       0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-01-01 00:00:00  
1       0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-01-01 00:05:00  
2       0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-01-01 00:10:00  
3       0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-01-01 00:15:00  
4       0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-01-01 00:20:00  
...     ...  ...  ...  ...  ...  ...  ...                  ...  
105115  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-12-31 23:35:00  
105116  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-12-31 23:40:00  
105117  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-12-31 23:45:00  
105118  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-12-31 23:50:00  
105119  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2018-12-31 23:55:00  

[105120 rows x 783 columns]

In [40]:
df_pressure_new.iloc[287:289]

0    1    2      3    4    5    6    7    8    9  ...  773  774  775  \
287  28.81  0.0  0.0  33.75  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
288  28.83  0.0  0.0  33.77  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   

     776  777  778  779  780  781             datetime  
287  0.0  0.0  0.0  0.0  0.0  0.0  2018-01-01 23:55:00  
288  0.0  0.0  0.0  0.0  0.0  0.0  2018-01-02 00:00:00  

[2 rows x 783 columns]

In [63]:
begin = datetime.date(2018,1,1)
end = datetime.date(2018,12,31)
graphs = []
for i in range((end - begin).days+1): # range(365)
    tmp_feature = []
    for node in G.nodes(): # 1-782
        tmp_feature.append(np.array(df_pressure_new.iloc[288*i : 288*(i+1), node-1].tolist()))
    G.graph["feature"] = csr_matrix(tmp_feature) 
    graphs.append(G)

In [64]:
len(graphs)

365

In [89]:
graphs[364].graph["feature"] # 9504/33 = 288 = (60/5) * 24

<782x288 sparse matrix of type '<class 'numpy.float64'>'
	with 9504 stored elements in Compressed Sparse Row format>

In [88]:
graphs[364][780][781]

{'weight': 0.5911166229382008, 'name': 'p901'}

In [75]:
save_path = './data/graphs/graph.pkl'
with open(save_path, "wb") as f:
    pkl.dump(graphs, f)
print("Processed Data Saved at {}".format(save_path))

Processed Data Saved at ./data/graphs/graph.pkl


In [79]:
with open(save_path, "rb") as f:
    graphs_load = pkl.load(f)
print("Loaded {} graphs".format(len(graphs_load)))

Loaded 365 graphs


## Run `EPANET` Simulation

In [19]:
print('Running EPANET simulation to generate nominal pressure data...\n') 

# We run an EPANET simulation using the WNTR library and the EPANET
# nominal model supplied with the BattLeDIM competition. 
# With this simulation, we have a complete pressure signal for all
# nodes in the network, on which the GNN algorithm is to be trained.

# Instantiate the nominal WDN model
nominal_wdn_model = epanetSimulator(path_to_wdn, 'data/l-town-data/')

# Run a simulation
nominal_wdn_model.simulate()

# Retrieve the nodal pressures
nominal_pressure = nominal_wdn_model.get_simulated_pressure()

Running EPANET simulation to generate nominal pressure data...



## Prepare Feature- and Label Matrices

In [20]:
x,y = dataCleaner(pressure_df    = nominal_pressure, # Pass the nodal pressures
                  observed_nodes = sensors,          # Indicate which nodes have sensors
                  rescale        = 'standard')       # Perform scaling on the timeseries data

# Split the data into training and validation sets
x_trn, x_val, y_trn, y_val = train_test_split(x, y, 
                                              test_size    = 0.2,
                                              random_state = 1,
                                              shuffle      = False)

ValueError: too many values to unpack (expected 2)

## What does the nominal pressure data look like?

Let's see how the `x_trn` and `y_trn` matrices look like:

## `x_trn`

In [25]:
pd.DataFrame(x_trn[:,:,0])

0    1    2         3    4    5    6    7    8    9    ...  772  \
0     0.829946  0.0  0.0  0.826284  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
1     0.860144  0.0  0.0  0.856257  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
2     0.890548  0.0  0.0  0.886465  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
3     0.921010  0.0  0.0  0.916726  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
4     0.951414  0.0  0.0  0.946980  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
...        ...  ...  ...       ...  ...  ...  ...  ...  ...  ...  ...  ...   
1608 -0.096818  0.0  0.0 -0.095607  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
1609 -0.114062  0.0  0.0 -0.112992  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
1610 -0.131236  0.0  0.0 -0.130322  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
1611 -0.148445  0.0  0.0 -0.147699  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
1612 -0.165727  0.0  0.0 -0.165122  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   

      773  774  775  776  777  778  779  780  781  
0     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
3     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
4     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
...   ...  ...  ...  ...  ...  ...  ...  ...  ...  
1608  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1609  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1610  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1611  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1612  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[1613 rows x 782 columns]

## `y_trn`

In [26]:
pd.DataFrame(y_trn[:,:,0])

0         1         2         3         4         5         6    \
0     0.829946  0.828731  0.828731  0.826284  0.824511  0.826186  0.829586   
1     0.860144  0.858713  0.858717  0.856257  0.854076  0.856120  0.859707   
2     0.890548  0.888925  0.888929  0.886465  0.883884  0.886286  0.890018   
3     0.921010  0.919175  0.919177  0.916726  0.913794  0.916508  0.920387   
4     0.951414  0.949407  0.949389  0.946980  0.943704  0.946710  0.950717   
...        ...       ...       ...       ...       ...       ...       ...   
1608 -0.096818 -0.095088 -0.095079 -0.095607 -0.092270 -0.095233 -0.096064   
1609 -0.114062 -0.112466 -0.112457 -0.112992 -0.109867 -0.112651 -0.113349   
1610 -0.131236 -0.129742 -0.129753 -0.130322 -0.127433 -0.129996 -0.130565   
1611 -0.148445 -0.147101 -0.147092 -0.147699 -0.145006 -0.147395 -0.147831   
1612 -0.165727 -0.164494 -0.164486 -0.165122 -0.162650 -0.164852 -0.165179   

           7         8         9    ...       772       773       774  \
0     0.823699  0.826294  0.828713  ...  0.242028  0.245499  0.243194   
1     0.853171  0.856268  0.858696  ...  0.311564  0.314994  0.312694   
2     0.882894  0.886467  0.888889  ...  0.380575  0.383985  0.381718   
3     0.912687  0.916728  0.919140  ...  0.447642  0.450988  0.448752   
4     0.942527  0.946967  0.949372  ...  0.512011  0.515301  0.513118   
...        ...       ...       ...  ...       ...       ...       ...   
1608 -0.091477 -0.095597 -0.095090  ...  0.022547  0.020153  0.021742   
1609 -0.109152 -0.113005 -0.112445  ...  0.032142  0.029753  0.031348   
1610 -0.126757 -0.130319 -0.129746  ...  0.041652  0.039277  0.040852   
1611 -0.144401 -0.147688 -0.147081  ...  0.050310  0.047960  0.049534   
1612 -0.162100 -0.165135 -0.164494  ...  0.058031  0.055665  0.057250   

           775       776       777       778       779       780       781  
0    -0.175023 -0.092034 -0.095805 -0.098831 -0.090101 -0.087512 -0.093492  
1    -0.105966 -0.022114 -0.025913 -0.028945 -0.020152 -0.017514 -0.023534  
2    -0.037211  0.047502  0.043687  0.040640  0.049493  0.052149  0.046102  
3     0.029819  0.115359  0.111526  0.108458  0.117369  0.120075  0.114000  
4     0.094419  0.180764  0.176936  0.173854  0.182805  0.185531  0.179441  
...        ...       ...       ...       ...       ...       ...       ...  
1608  0.311030  0.254486  0.256896  0.258871  0.252806  0.250663  0.254761  
1609  0.319179  0.262865  0.265244  0.267215  0.261173  0.259066  0.263140  
1610  0.327236  0.271139  0.273499  0.275467  0.269466  0.267354  0.271415  
1611  0.334537  0.278648  0.280992  0.282938  0.276984  0.274878  0.278909  
1612  0.341011  0.285288  0.287610  0.289548  0.283623  0.281544  0.285550  

[1613 rows x 782 columns]